In [1]:
from configuracoes_notebooks import set_proj_dir
set_proj_dir()

O diretorio do seu projeto é coleta_cebrap
Caminho absoluto do diretorio encontrado C:\Users\x526378\Desktop\projetos\cebrap\coleta_cebrap
Caminho no path.


In [2]:
import os
import geopandas as gpd
import pandas as pd

from notebooks.jupyter import utils
from utils import (
    get_data_diretorio,
    save_parquet_excel,
)
from utils.downloads import _prepare_cache

# População a menos de 1km de parques urbanos e lineares

Pessoas de outras cidades também estão dentro das áreas de 1km de parques, porém optei por não considerá-las ao fazer a contagem.

Eu interpretei esse título como <=1km, não como <1km

In [3]:
data_path = get_data_diretorio()

In [4]:
assets_path = os.path.join(
    data_path,
    'assets'
)

# Dependências

Este notebook depende dos arquivos resultantes dos notebooks '.overlay_setores22_buff_parq', '.buffed_parques_urb_line' '../../arborizacao_viaria/carregar_dados/malha_distritos' e '../load_data//malha_parques_lineares_urbanos'

In [5]:
gdf_distritos = gpd.read_parquet(
    os.path.join(
        assets_path,
        'distrito_ibge.parquet'
    )
)

In [6]:
gdf_parq_urb_line=gpd.read_parquet(
    os.path.join(
        assets_path,
        'parques_urbanos_e_lineares.parquet'
    )
)

In [7]:
gdf_buffed_setor = gpd.read_parquet(
    os.path.join(
        assets_path,
        'parques_lineares_e_urbanos',
        'overlay_setores22_buff_parques_urb_line.parquet'        
    )
)

In [8]:
gdf_buffed  = gpd.read_parquet(
    os.path.join(
        assets_path,
        'parques_lineares_e_urbanos',
        'area_1km_parques_urbanos_lineares.parquet'
    )
)

# Somar população de setores recortados por distrito

In [9]:
gdf_distritos.columns

Index(['CD_MUN', 'NM_MUN', 'CD_DIST', 'NM_DIST', 'CD_RGINT', 'NM_RGINT',
       'CD_RGI', 'NM_RGI', 'CD_CONCURB', 'NM_CONCURB', 'AREA_KM2', 'total_pop',
       'total_dom', 'geometry'],
      dtype='object')

In [10]:
for i, distrito in gdf_distritos.iterrows():
     gdf_distritos.loc[gdf_distritos.index==i, 'pop_dist_recort'] = sum(
        gdf_buffed_setor
        .loc[gdf_buffed_setor['CD_DIST']==distrito['CD_DIST'], 'pop_recort']
    )

In [11]:
gdf_distritos.sample(3)

CD_MUN     NM_MUN    CD_DIST       NM_DIST CD_RGINT   NM_RGINT  CD_RGI  \
7   3550308  São Paulo  355030808         BELEM     3501  São Paulo  350001   
75  3550308  São Paulo  355030876     SAPOPEMBA     3501  São Paulo  350001   
94  3550308  São Paulo  355030895  SAO DOMINGOS     3501  São Paulo  350001   

       NM_RGI CD_CONCURB    NM_CONCURB   AREA_KM2  total_pop total_dom  \
7   São Paulo    3550308  São Paulo/SP   6.121560      55785     25449   
75  São Paulo    3550308  São Paulo/SP  13.618175     266715    105579   
94  São Paulo    3550308  São Paulo/SP   9.914590      88884     37746   

                                             geometry  pop_dist_recort  
7   POLYGON ((337329.398 7395388.459, 337268.595 7...           5668.0  
75  POLYGON ((345916.57 7386712.024, 345909.731 73...         264804.0  
94  POLYGON ((321653.073 7399213.8, 321651.611 739...          66353.0

# Conferir

A partir do mapa, vamos conferir o caso de um distrito que consta com um valor baixo de pop na área de 1km dos parques lineares, Cursino.

In [12]:
m= gdf_distritos.explore(color='grey')

gdf_distritos.loc[gdf_distritos['CD_DIST']=='355030827'].explore(m=m)

gdf_buffed.explore(
    m=m,
    color="pink"
)

gdf_parq_urb_line.explore(
    m=m,
    color='red'
)

gdf_buffed_setor.loc[gdf_buffed_setor['CD_DIST']=='355030827'].explore(
    m=m,
    color="aquamarine"
)

Aqui tem os distritos que não tem nenhuma pessoa a 1km ou menos de parques lineares e urbanos.

In [13]:
(
    gdf_distritos
    .loc[gdf_distritos['pop_dist_recort']==gdf_distritos['pop_dist_recort']
    .min()]
)

CD_MUN     NM_MUN    CD_DIST   NM_DIST CD_RGINT   NM_RGINT  CD_RGI  \
51  3550308  São Paulo  355030852  MARSILAC     3501  São Paulo  350001   
67  3550308  São Paulo  355030868    SACOMA     3501  São Paulo  350001   
78  3550308  São Paulo  355030879   SOCORRO     3501  São Paulo  350001   

       NM_RGI CD_CONCURB    NM_CONCURB    AREA_KM2  total_pop total_dom  \
51  São Paulo    3550308  São Paulo/SP  207.501260      11451      6139   
67  São Paulo    3550308  São Paulo/SP   14.610797     261436    113894   
78  São Paulo    3550308  São Paulo/SP   12.261579      38051     16549   

                                             geometry  pop_dist_recort  
51  POLYGON ((333016.008 7354600.919, 333056.044 7...              0.0  
67  POLYGON ((338605.158 7385601.06, 338598.678 73...              0.0  
78  POLYGON ((326832.519 7378799.896, 326814.871 7...              0.0

Aqui é o distrito com a menor quantidade de pessoas a 1km ou menos de parques lineares e urbanos, menos os que estão zerados

In [14]:
distritos_sem0=gdf_distritos.loc[gdf_distritos['pop_dist_recort']!=0.0]
(
    distritos_sem0
    .loc[distritos_sem0['pop_dist_recort']==distritos_sem0['pop_dist_recort']
    .min()]
)

CD_MUN     NM_MUN    CD_DIST  NM_DIST CD_RGINT   NM_RGINT  CD_RGI  \
26  3550308  São Paulo  355030827  CURSINO     3501  São Paulo  350001   

       NM_RGI CD_CONCURB    NM_CONCURB   AREA_KM2  total_pop total_dom  \
26  São Paulo    3550308  São Paulo/SP  12.060052     103171     46155   

                                             geometry  pop_dist_recort  
26  POLYGON ((335822.146 7385759.521, 335833.043 7...            131.0

Aqui vemos o distrito com a maior quantidade de pessoas a 1km ou menos dos parques.

In [15]:
(
    gdf_distritos
    .loc[gdf_distritos['pop_dist_recort']==gdf_distritos['pop_dist_recort']
    .max()]
)

CD_MUN     NM_MUN    CD_DIST NM_DIST CD_RGINT   NM_RGINT  CD_RGI  \
29  3550308  São Paulo  355030830  GRAJAU     3501  São Paulo  350001   

       NM_RGI CD_CONCURB    NM_CONCURB   AREA_KM2  total_pop total_dom  \
29  São Paulo    3550308  São Paulo/SP  92.578049     384873    154205   

                                             geometry  pop_dist_recort  
29  POLYGON ((327239.195 7362453.213, 327195.452 7...         279532.0

# Calcular a porcentagem da pop_recort

Já temos a quantidade de pessoas por distrito, mas o indicador é: % da população a menos de 1 km de parques urbanos e lineares, que é 

População total (do distrito) / População a 1km ou menos de parques (no distrito)

In [16]:
gdf_distritos['pct_pop_recort']= (
    gdf_distritos['pop_dist_recort']/gdf_distritos['total_pop']
)

In [17]:
gdf_distritos.sample(3)

CD_MUN     NM_MUN    CD_DIST         NM_DIST CD_RGINT   NM_RGINT  CD_RGI  \
50  3550308  São Paulo  355030851        MANDAQUI     3501  São Paulo  350001   
64  3550308  São Paulo  355030865  RAPOSO TAVARES     3501  São Paulo  350001   
53  3550308  São Paulo  355030854         MORUMBI     3501  São Paulo  350001   

       NM_RGI CD_CONCURB    NM_CONCURB   AREA_KM2  total_pop total_dom  \
50  São Paulo    3550308  São Paulo/SP  13.202709     103665     45143   
64  São Paulo    3550308  São Paulo/SP  12.164313     117738     49006   
53  São Paulo    3550308  São Paulo/SP  11.462372      43690     20710   

                                             geometry  pop_dist_recort  \
50  POLYGON ((332902.165 7405221.112, 332904.48 74...           6015.0   
64  POLYGON ((319022.919 7388900.499, 318990.285 7...         117738.0   
53  POLYGON ((325192.046 7387331.143, 325166.217 7...          23335.0   

    pct_pop_recort  
50        0.058023  
64        1.000000  
53        0.534104

# Conferir

Novamente vamos checar vendo se os mínimos e máximos fazem sentido.

Aqui tem os distritos que não tem nenhuma pessoa a 1km ou menos de parques lineares e urbanos.

In [18]:
(
    gdf_distritos
    .loc[gdf_distritos['pct_pop_recort']==gdf_distritos['pct_pop_recort']
    .min()]
)

CD_MUN     NM_MUN    CD_DIST   NM_DIST CD_RGINT   NM_RGINT  CD_RGI  \
51  3550308  São Paulo  355030852  MARSILAC     3501  São Paulo  350001   
67  3550308  São Paulo  355030868    SACOMA     3501  São Paulo  350001   
78  3550308  São Paulo  355030879   SOCORRO     3501  São Paulo  350001   

       NM_RGI CD_CONCURB    NM_CONCURB    AREA_KM2  total_pop total_dom  \
51  São Paulo    3550308  São Paulo/SP  207.501260      11451      6139   
67  São Paulo    3550308  São Paulo/SP   14.610797     261436    113894   
78  São Paulo    3550308  São Paulo/SP   12.261579      38051     16549   

                                             geometry  pop_dist_recort  \
51  POLYGON ((333016.008 7354600.919, 333056.044 7...              0.0   
67  POLYGON ((338605.158 7385601.06, 338598.678 73...              0.0   
78  POLYGON ((326832.519 7378799.896, 326814.871 7...              0.0   

    pct_pop_recort  
51             0.0  
67             0.0  
78             0.0

Aqui é o distrito com a menor quantidade de pessoas a 1km ou menos de parques lineares e urbanos, menos os que estão zerados

In [19]:
distritos_sem0=gdf_distritos.loc[gdf_distritos['pct_pop_recort']!=0.0]
(
    distritos_sem0
    .loc[distritos_sem0['pct_pop_recort']==distritos_sem0['pct_pop_recort']
    .min()]
)

CD_MUN     NM_MUN    CD_DIST  NM_DIST CD_RGINT   NM_RGINT  CD_RGI  \
26  3550308  São Paulo  355030827  CURSINO     3501  São Paulo  350001   

       NM_RGI CD_CONCURB    NM_CONCURB   AREA_KM2  total_pop total_dom  \
26  São Paulo    3550308  São Paulo/SP  12.060052     103171     46155   

                                             geometry  pop_dist_recort  \
26  POLYGON ((335822.146 7385759.521, 335833.043 7...            131.0   

    pct_pop_recort  
26         0.00127

Aqui vemos o distrito com a maior quantidade de pessoas a 1km ou menos dos parques.

In [20]:
(
    gdf_distritos
    .loc[gdf_distritos['pct_pop_recort']==gdf_distritos['pct_pop_recort']
    .max()]
)

CD_MUN     NM_MUN    CD_DIST         NM_DIST CD_RGINT   NM_RGINT  CD_RGI  \
64  3550308  São Paulo  355030865  RAPOSO TAVARES     3501  São Paulo  350001   
93  3550308  São Paulo  355030894      VILA SONIA     3501  São Paulo  350001   

       NM_RGI CD_CONCURB    NM_CONCURB   AREA_KM2  total_pop total_dom  \
64  São Paulo    3550308  São Paulo/SP  12.164313     117738     49006   
93  São Paulo    3550308  São Paulo/SP  10.066693     123748     53826   

                                             geometry  pop_dist_recort  \
64  POLYGON ((319022.919 7388900.499, 318990.285 7...         117738.0   
93  POLYGON ((323710.87 7387720.911, 323703.262 73...         123748.0   

    pct_pop_recort  
64             1.0  
93             1.0

# Salvar

In [21]:
save_parquet_excel(
    gdf_distritos,
    'pop_1km_parques_urbanos_lineares',
    assets_path,
    'parques_lineares_e_urbanos'
)